In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
from sentinelhub import SentinelHubRequest, DataCollection, MimeType, CRS, BBox, SHConfig
from dotenv import load_dotenv
from pyproj import Transformer
import os
import numpy as np
import matplotlib.pyplot as plt
import rasterio
import folium
import cv2
from urban_watch.ml_logic.data import load_data
from s2cloudless import S2PixelCloudDetector
from urban_watch.ml_logic.package import CloudMasker
from urban_watch.ml_logic.package import preprocess_image

import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score,RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from xgboost import XGBClassifier

from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix, roc_auc_score

import time

In [ ]:
from sentinelhub import SHConfig
from dotenv import load_dotenv
import os

In [ ]:
from urban_watch.interface.main import full_preproc_pipeline
from urban_watch.interface.main import train
from urban_watch.interface.main import evaluate
#  Entrainement d'un nouveau modele
X,y = full_preproc_pipeline()
metrics = train(X,y, model_type="random_forest")

In [2]:
import requests
url = "http://localhost:8000/predict"
params = {
    "date": "2021-06-15",
    "lon": 0.10432014043169194,
    "lat": 43.23224498737862,
    "size_km": 3
}
response = requests.get(url, params=params)

In [3]:
response=response.json()
response


{'urbanization_score': 0.29,
 'prediction': [[1,
   1,
   1,
   1,
   0,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   0,
   0,
   1,
   1,
   0,
   0,
   1,
   0,
   0,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   1,
   0,
   0,
   0,
   0,
   0,
   1,
   1,
   1,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   1,
   1,
   1,
   1,
   1,
   1,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   0,
   1,
   1,
   0,
   0,
   0,
   0,
   0,
   1,
   1,
   0,
   0,
   0,
   0,
   0,
   

In [6]:
import numpy as np
import pandas as pd
y_pred = np.array(response["prediction"])
rgb = np.array(response["rgb"])
print("Prediction shape:", y_pred.shape)
print("RGB shape:", rgb.shape)
pd.DataFrame(y_pred)[0].value_counts()

Prediction shape: (290, 312)
RGB shape: (290, 312, 3)


0
 1    139
 0    106
-1     45
Name: count, dtype: int64

In [ ]:
load_dotenv()  # charge automatiquement le .env du dossier courant

config = SHConfig()
config.sh_client_id = os.environ.get("SH_CLIENT_ID")
config.sh_client_secret = os.environ.get("SH_CLIENT_SECRET")

In [ ]:
list_bbox_centers = [(43.52960344286241, 5.448962145567533),
(48.092094070852475, -1.7036876101196967),
 (48.121222106840435, -1.602864906604979),
 (45.74557103359813, 4.803091960652229),
 (47.8776770361181, -3.909947991759771),
 (44.55378060775165, 4.28389205759154),
 (45.69764498502806, 5.8945655967385315),
 (48.07500134978729, 7.3491231648955155),
 (50.63412206750312, 3.0435779303880106),
 (44.83078182200822, 0.5108123933396876)]

In [ ]:
from urban_watch.ml_logic.data import make_bbox_global, get_data

data = get_data(list_bbox_centers, config)

In [ ]:
from urban_watch.ml_logic.data import load_data

X, meta = load_data()
print("shape de x:", X.shape)
print("Nombre de NaN dans X brut :", np.isnan(X).sum())

In [ ]:
from urban_watch.ml_logic.labels import get_bbox_from_features, bbox_to_wgs84

list_bbox, list_crs = get_bbox_from_features()
list_bbox_wgs84 = bbox_to_wgs84(list_bbox, list_crs)

In [ ]:
from urban_watch.ml_logic.labels import tile_name_from_bbox_wgs84

tile_names = tile_name_from_bbox_wgs84(list_bbox_wgs84)

In [ ]:
from urban_watch.ml_logic.labels import get_label_array

results = get_label_array(tile_names, list_bbox_wgs84, list_bbox, list_crs)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap

# Exemple palette simplifiée
colors = [
    "#006400",  # 10 Trees
    "#ffbb22",  # 20 Shrub
    "#ffff4c",  # 30 Grass
    "#f096ff",  # 40 Crop
    "#fa0000",  # 50 Built-up
    "#b4b4b4",  # 60 Bare
    "#f0f0f0",  # 70 Snow
    "#0064c8",  # 80 Water
    "#0096a0",  # 90 Wetlands
    "#00cf75",  # 95 Mangroves
    "#fae6a0"   # 100 Moss/Lichen
]

cmap = ListedColormap(colors)
y_list =results
y = np.array(y_list)

print("Labels uniques :", np.unique(y))
print("Shape y:", y.shape)


debut du test train model avec le Y


In [ ]:
X_list = []
y_list = []
for i in range(X.shape[0]):
    img = X[i]
    label = y[i]

    X_processed, mask_valid= preprocess_image(img)

    y_flat = label.reshape(-1)
    y_valid = y_flat[mask_valid.reshape(-1)]

    X_list.append(X_processed)
    y_list.append(y_valid)

X_all = np.vstack(X_list)
y_all = np.hstack(y_list)

print("X_all", X_all.shape)
print("y_all", y_all.shape)
print("nan dans xall", np.isnan(X_all).sum())


In [ ]:
y_binary = (y_all == 50).astype(int)
non_urbain_count = (y_binary == 0).sum()
urbain_count = (y_binary == 1).sum()
print(f"  Non-urbain: {non_urbain_count} ({100*non_urbain_count/(non_urbain_count+urbain_count):.1f}%)")
print(f"  Urbain: {urbain_count} ({100*urbain_count/(non_urbain_count+urbain_count):.1f}%)")


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    X_all, y_binary, test_size=0.2, random_state=42, stratify=y_binary
)
print(f"Train set: {X_train.shape} | Test set: {X_test.shape}")

In [ ]:
#_________________________________________________

In [ ]:
all_results = []
#fonction pour evaluer le modele
def evaluate_model(param_grid,
                   X_train, X_test, y_train, y_test,
                   model_name, n_iter=12):
    if model_name == "Random Forest":
        model = RandomForestClassifier(random_state=42, n_jobs=-1, class_weight='balanced')
        search = RandomizedSearchCV(
            model,
            param_distributions=param_grid,
            n_iter=n_iter,
            cv=3,
            scoring='f1',
            n_jobs=-1,
            random_state=42
        )
    else:
        if model_name == "Gradient Boosting":
            model = GradientBoostingClassifier(random_state=42)
            search = GridSearchCV(
                model,
                param_grid=param_grid,
                cv=3,
                scoring='f1',
                n_jobs=-1
            )
        elif model_name == "XGBoost":
            model = XGBClassifier(random_state=42, use_labels_encoder = False, eval_metric='logloss', tree_method='hist', n_jobs=1)
            search = RandomizedSearchCV(
                model,
                param_distributions=param_grid,
                n_iter=10,
                cv=3,
                scoring='f1',
                n_jobs=1,
                verbose=1
            )
        elif model_name == "Logistic Regression":
            model= LogisticRegression(random_state=42, max_iter=1000)
            search = GridSearchCV(
                model,
                param_grid=param_grid,
                cv=3,
                scoring='f1',
                n_jobs=-1
            )




    search.fit(X_train, y_train)

    best_model= search.best_estimator_
    best_params= search.best_params_

    for param, value in best_params.items():
        print(f"{param} : {value}")

    y_pred = best_model.predict(X_test)
    y_pred_proba = best_model.predict_proba(X_test)[:,1]

    acc= accuracy_score(y_test, y_pred)
    prec= precision_score(y_test, y_pred)
    rec= recall_score(y_test, y_pred)
    f1= f1_score(y_test, y_pred)
    roc_auc= roc_auc_score(y_test, y_pred_proba)

    print(f"   Accuracy:  {acc:.4f}")
    print(f"   Precision: {prec:.4f}")
    print(f"   Recall:    {rec:.4f}")
    print(f"   F1-Score:  {f1:.4f}")
    print(f"   ROC-AUC:   {roc_auc:.4f}")

    cv_scores= cross_val_score(best_model, X_train, y_train, cv=5, scoring='f1')
    cv_mean= cv_scores.mean()
    cv_std= cv_scores.std()

    print(f"cv f1 score: {cv_scores}")
    print(f"mean: {cv_mean} / ({cv_std})")

    cm = confusion_matrix(y_test, y_pred)
    tn, fp, fn, tp = cm.ravel()
    specificity = tn/(tn+fp) if (tn+fp) >0 else 0

    print(f"confusion de matrix")
    print(f"tp : {tp} | fp: {fp}")
    print(f"fn : {fn} | tn: {tn}")
    print(f"specificity : {specificity}")

    result = {
        "Model":model_name,
        'Best_Params': str(best_params),
        'Accuracy': acc,
        'Precision': prec,
        'Recall': rec,
        'F1-Score': f1,
        'ROC-AUC' : roc_auc,
        'CV_Mean': cv_mean,
        'CV_Std': cv_std,
        'Specificity': specificity

    }
    return best_model, result, cm


In [ ]:
rf_params = {
    'n_estimators': [150], #200-250
    'max_depth': [10, 20],
    'min_samples_split': [2, 10],
    'min_samples_leaf': [1]
}
rf_best, rf_result, rf_cm = evaluate_model(rf_params, X_train, X_test, y_train, y_test, "Random Forest")
all_results.append(rf_result)

In [ ]:
xgb_params = {
    'n_estimators': [100,200],
    'learning_rate': [0.01,0.05, 0.1],
    'max_depth': [3,5,7],
    'subsample':[0.8,1]
}
xgb_best, xgb_result, xgb_cm = evaluate_model(xgb_params, X_train, X_test, y_train, y_test, "XGBoost")
all_results.append(xgb_result)

In [ ]:
lr_params = {
    'C': [0.001,0.01,0.1,1],
    'solver': ['lgbfs', 'liblinear']
}
lr_best, lr_result, lr_cm = evaluate_model(lr_params, X_train, X_test, y_train, y_test, "Logistic Regression")
all_results.append(lr_result)

In [ ]:
df_results = pd.DataFrame(all_results)
summary_df = df_results[['Model','Accuracy','Precision','Recall', 'F1-Score','ROC-AUC', 'CV_Mean', 'Specificity']].copy()
summary_df= summary_df.sort_values('F1-Score', ascending=False).reset_index(drop=True)
print(summary_df.to_string(index=True))

In [ ]:
best_idx = summary_df.index[0]
best_model_name = summary_df.loc[best_idx, 'Model']
best_f1 = summary_df.loc[best_idx, 'F1-Score']
print(best_model_name)
print(best_f1)

In [ ]:
fig, axes = plt.subplots(2, 3, figsize=(16, 10))

metrics = ['Accuracy', 'Precision', 'Recall', 'F1-Score', 'ROC-AUC', 'CV_Mean']
colors = ['steelblue', 'coral', 'lightgreen', 'orange', 'skyblue', 'plum']

for idx, (ax, metric, color) in enumerate(zip(axes.flat, metrics, colors)):
    values = summary_df[metric].values
    models = summary_df['Model'].values
    bars = ax.bar(range(len(models)), values, color=color)
    ax.set_ylabel(metric, fontweight='bold')
    ax.set_title(f'{metric}', fontweight='bold', fontsize=12)
    ax.set_xticks(range(len(models)))
    ax.set_xticklabels(models, rotation=45, ha='right', fontsize=10)
    ax.set_ylim([0, 1.05])

    for bar in bars:
        height = bar.get_height()
        ax.text(bar.get_x() + bar.get_width()/2., height,
                f'{height:.3f}', ha='center', va='bottom', fontsize=9)

plt.tight_layout()
plt.show()

print("✅ Analyse complète terminée!")

In [ ]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(
    n_estimators=200,
    max_depth=20,
    n_jobs=-1
)

clf.fit(X_all, y_all)
print("Accuracy :", clf.score(X_all, y_all))

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(
    X_all, y_all,
    test_size=0.4,
    random_state=42,
    stratify=y_all
)


from sklearn.ensemble import RandomForestClassifier

clf = RandomForestClassifier(
    n_estimators=300,
    max_depth=25,
    n_jobs=-1,
    random_state=42
)

clf.fit(X_train, y_train)
train_acc = clf.score(X_train, y_train)
test_acc  = clf.score(X_test, y_test)

print("Accuracy train :", train_acc)
print("Accuracy test :", test_acc)